In [ ]:
# imageFormation-sensors

import numpy as np
import matplotlib.pyplot as plt

N  = 256
im = np.zeros((N,N,3))
for i in range(0,N):
    im[i,:,0] = i*0.0039
    im[i,:,1] = 1-i*0.0039
    im[i,:,2] = 1
plt.imshow(im)

In [ ]:
# imageFormation-distortions

from warping import *
import matplotlib.pyplot as plt

# load square, grayscale image
im  = Image.open('HanyFaridDistort.jpg')
[ydim,xdim] = im.size
mid = round(max(xdim,ydim)/2)

# define sampling lattices
n   = 100 # latice sampling
dst = griddify(shape_to_rect(im.size), n, n) # destination grid
src = dst # source grid 

# define new sampling lattice (src)
k = 0.0000005 # estimated lens distortion
dst = dst - mid # put image center at (0,0)
for i in range(n+1):
    for j in range(n+1):
        x = dst[i,j,0]
        y = dst[i,j,1]
        r = np.sqrt( x**2 + y**2 )
        src[i,j,0] = x * (1 + k*r**2)
        src[i,j,1] = y * (1 + k*r**2)

dst  = dst + mid # re-center
dst  = dst.astype(int) # convert to integer
src  = src + mid # re-center
src  = src.astype(int) # convert to integer

# warp image
mesh = grid_to_mesh(src, dst) # define mesh
imt  = im.transform(im.size, Image.MESH, mesh) # warp
plt.figure(figsize=(ydim/72,xdim/72))
plt.subplot(1,2,1)
plt.imshow(im,cmap='gray')
plt.subplot(1,2,2)
plt.imshow(imt,cmap='gray')
plt.show()

In [ ]:
# JPEG-DCT
import numpy as np

# input:  B: 8x8 image-pixel block
#         Q: 8x8 quantization (integer-valued)
# output: D: 8x8 block-DCT
def dct2(B,Q):
    D = np.zeros((8,8)) # initialize
    y,x = np.meshgrid(np.arange(1,9,1), np.arange(1,9,1))
    for i in range(1,9):
        for j in range(1,9):
            ai = np.sqrt(1/8) if i == 1 else np.sqrt(2/8)
            aj = np.sqrt(1/8) if j == 1 else np.sqrt(2/8)
            D[i-1,j-1] = ai * aj * np.sum( np.sum(B * np.cos(np.pi*(2*x-1)*(i-1)/16) * 
                                                      np.cos(np.pi*(2*y-1)*(j-1)/16)) )
    return( np.array( D/Q, dtype=int) ) # quantize

B = 255*np.random.rand(8,8) # image block 
Q = 2*np.ones((8,8)) # quantization table
dct2(B,Q)